In [116]:
import torch
import pandas
import numpy as np

In [3]:
import pandas
#dataset taken from https://www.kaggle.com/yashsawarn/wifi-stretgth-for-rooms

def read_dataset(csv_name = 'wifi_localization.txt'):
    """
    Reads a csv dataset 
    returns it as a pytorch tensor
    """
    data_frame = pandas.read_table(csv_name, delim_whitespace=True, names=('A', 'B', 'C', 'D','E', 'F', 'G', 'ROOM'),
                       dtype={'A': np.int64, 'B': np.float64, 'C': np.float64, 'D': np.float64,'E': np.float64,'F': np.float64,'G': np.float64,'ROOM': np.float64})

    targets_torch = torch.tensor(data_frame['ROOM'].values)
    dataset_torch = torch.tensor(data_frame.values)
    print("dataset torch ", dataset_torch.shape)
    return dataset_torch
dataset_torch = read_dataset()


dataset torch  torch.Size([2000, 8])


In [117]:
class Node_CART:    
    def __init__(self, num_classes = 4, ref_CART = None, current_depth = 0, use_gini=True):
        """
        Create the node attributes
        param num_classes: K number of classes to classify
        param ref_cart: reference to the tree containing the node
        param current_depth: current depth of the node in the tree
        """
        self.ref_CART = ref_CART
        self.threshold_value = 0
        self.feature_num = 0
        self.node_right = None
        self.node_left = None
        self.data_torch_partition = None
        self.gini = 0
        self.use_gini = use_gini
        self.dominant_class = None
        self.accuracy_dominant_class = None        
        self.num_classes = num_classes
        self.current_depth = current_depth
    
    def to_xml(self, current_str = ""):
        """
        Recursive function to write the node content to an xml formatted string
        param current_str : the xml content so far in the whole tree
        return the string with the node content
        """
        str_node = "<node><thresh>" + str(self.threshold_value) + "</thresh>" + "<feature>" + str(self.feature_num) + "</feature><depth>" + str(self.current_depth)+ "</depth>" 
        str_node += "<gini>" + str(self.gini) + "</gini>"
        if(self.node_right != None):
            str_left = self.node_right.to_xml(current_str)
            str_node += str_left
        if(self.node_left != None):
            str_right = self.node_left.to_xml(current_str)
            str_node += str_right
            
        if(self.is_leaf()):
            str_node += "<dominant_class>" + str(self.dominant_class) + "</dominant_class><acc_dominant_class>"  + str(self.accuracy_dominant_class) + "</acc_dominant_class>"
        str_node += "</node>"
        return str_node
    
    def is_leaf(self):
        """
        Checks whether the node is a leaf
        """
        return (self.node_left == None and self.node_right == None)
    
    def create_with_children(self, data_torch, current_depth, list_selected_features = [], min_gini = 0.000001):
        """
        Creates a node by selecting the best feature and threshold, and if needed, creating its children
        param data_torch: dataset with the current partition to deal with in the node
        param current_depth: depth counter for the node
        param list_selected_features: list of selected features so far for the CART building process
        param min_gini: hyperparmeter selected by the user defining the minimum tolerated gini coefficient for a  node
        return the list of selected features so far
        """        
        #update depth of children
        depth_children = current_depth + 1
      
        if(depth_children <= self.ref_CART.get_max_depth()):
            num_observations = data_torch.shape[0]            
            #careful with max depth
            #if no threshold and feature were selected, select it using a greedy approach            
            (threshold_value, feature_num, gini) = self.select_best_feature_and_thresh(data_torch, list_features_selected = [])
            list_selected_features += [feature_num]
            #store important data in attributes
            self.threshold_value = threshold_value
            self.feature_num = feature_num
            self.data_torch_partition = data_torch
            self.gini = gini            
            num_features = data_torch.shape[1]

            #create the right and left node data if the current gini is still high            
            if(self.gini > min_gini): 
                data_torch_left = data_torch[data_torch[:, feature_num] < threshold_value]
                data_torch_right = data_torch[data_torch[:, feature_num] >= threshold_value]

                #if the new partitions have more than min_observations, make them
                if(data_torch_left.shape[0] >= self.ref_CART.get_min_observations() and data_torch_right.shape[0] >= self.ref_CART.get_min_observations()):
                    #add data to the right and left children

                    self.node_right = Node_CART(num_classes = self.num_classes, ref_CART = self.ref_CART, current_depth = depth_children, use_gini=self.use_gini)
                    self.node_left = Node_CART(num_classes = self.num_classes, ref_CART = self.ref_CART, current_depth = depth_children, use_gini=self.use_gini)
                    list_selected_features = self.node_right.create_with_children(data_torch_right, depth_children, list_selected_features = list_selected_features)            
                    self.node_left.create_with_children( data_torch_left, depth_children, list_selected_features = list_selected_features)
        #if is leaf, fill the         
        if(self.is_leaf()):            
            labels_data = data_torch[:,  -1]
            self.dominant_class = torch.mode(labels_data).values.item()
            num_obs_label = labels_data[labels_data == self.dominant_class].shape[0]
            self.accuracy_dominant_class = num_obs_label / labels_data.shape[0]           
            
        return list_selected_features
    
    
    def select_best_feature_and_thresh(self, data_torch, list_features_selected = [], num_classes = 4):
        """
        Selects the best feature and threshold that minimizes the gini coefficient
        param data_torch: dataset partition to analyze
        param list_features_selected list of features selected so far, thus must be ignored 
        param num_classes: number of K classes to discriminate from 
        return min_thresh, min_feature, min_gini found for the dataset partition when 
        selecting the found feature and threshold
        """       
        min_gini = 10
        threshold = 0
        min_feature = 0
        
        print('data_torch', data_torch)
        
        for feature_id in range(data_torch.shape[1]-1):
            print("------------- Feature id: {} -------------".format(feature_id))
            # Get all the values of the column
            column_values = data_torch[:,feature_id]
            
            # Sort tensor in ascending order
            values_sorted, _ = torch.sort(column_values)
            print('values_sorted', values_sorted)
            
            # Get the first value, and ignore it in the for.
            threshold_tmp = values_sorted[0].item()
            for value in values_sorted[1:]:
                print("------------- Feature id: {}, Value: {} -------------".format(feature_id, value.item()))
                if threshold_tmp == value.item():
                    print("Continue value:", value.item())
                    continue
                threshold_tmp = value.item()
                
                data_torch_left = data_torch[data_torch[:, feature_id] < threshold_tmp]
                data_torch_right = data_torch[data_torch[:, feature_id] >= threshold_tmp]
                
                print('Data < {}: {}'.format(value.item(), data_torch_left))
                print('Data > {}: {}'.format(value.item(), data_torch_right))
                
                if self.use_gini:
                    left_entropy = self.calculate_gini(data_torch_left[:,-1],num_classes=num_classes)
                    right_entropy = self.calculate_gini(data_torch_right[:,-1],num_classes=num_classes)
                else:
                    left_entropy = self.calculate_entropy(data_torch_left[:,-1],num_classes=num_classes)
                    right_entropy = self.calculate_entropy(data_torch_right[:,-1],num_classes=num_classes)
        
                
                print('left_entropy: ', left_entropy)
                print('right_entropy: ', right_entropy)
                
                # Calculate ponderate
                ponderate = self.get_ponderate(data_torch_left.shape[0], data_torch_right.shape[0], data_torch.shape[0], left_entropy, right_entropy)
                print('Ponderate: ',ponderate)
                
                if ponderate < min_gini:
                    min_gini = ponderate
                    threshold = threshold_tmp
                    min_feature = feature_id
        
        print('min_gini: {}, threshold: {}, min_feature: {} '.format(min_gini, threshold, min_feature))
        print('-----------------------------------------------------------------')
        return (threshold, min_feature, min_gini) 
    
    
    def calculate_gini(self, data_partition_torch, num_classes = 4):
        """
        Calculates the gini coefficient for a given partition with the given number of classes
        param data_partition_torch: current dataset partition as a tensor
        param num_classes: K number of classes to discriminate from
        returns the calculated gini coefficient
        """
        
        
        # Calculate the density of each class
        density = self.get_density(data_partition_torch, num_classes)
        
        # Calculate the entropy using the density array
        gini =  1 -  np.dot( density ,  density )
        print("gini:", gini)
        
        return gini
         
    
    def calculate_entropy(self, data_partition_torch, num_classes = 4):
        """
        Calculates the gini coefficient for a given partition with the given number of classes
        param data_partition_torch: current dataset partition as a tensor
        param num_classes: K number of classes to discriminate from
        returns the calculated entropy coefficient
        
        data_partition_torch = [1, 2, 2, 2, 3, 3, 3, 3, 3, 4]
        
        """
        
        # Calculate the density of each class
        density = self.get_density(data_partition_torch, num_classes)
        
        # Calculate the entropy using the density array
        entropy =  -1* np.dot( density ,  np.log2(density) )
        
        return entropy
    
    def get_density(self, data_partition_torch, num_classes):
        """
        Calculates the density of each class
        param data_partition_torch: current dataset partition as a tensor
        param num_classes: K number of classes
        returns: the calculated density array
        
        data_partition_torch = [1, 2, 2, 2, 3, 3, 3, 3, 3, 4]
        
        """
        data_len = data_partition_torch.shape[0]
        
        # Get the amount of each class from the data_partition_torch
        # Example of output: [0, 2, 3, 5, 6], ignore the first element
        
        #values = torch.bincount(data_partition_torch.int(),minlength=num_classes)
        values = torch.bincount(data_partition_torch.int(),minlength=num_classes+1)
        
        # Calculate the density of each class
        density = []
        
        #for value in values[0:]:
        for value in values[1:]:
            data = value/data_len + 0.000001
            if data == 0:
                data += 0.000001
            density.append(data)
        
        return density
    
    def get_ponderate(self, nl, nr, n, hl, hr):
        """
        Return the ponderate data.
        param nl: Number left observations
        param nr: Number riht observations
        param n: Total of observations
        param hl: Left value (entropy or gini)
        param hd: Right value (entropy or gini)
        
        """
        return (nr/n)*hr + (nl/n)*hl  
    
    def evaluate_node(self, input_torch): 
        """
        Evaluates an input observation within the node. 
        If is not a leaf node, send it to the corresponding node
        return predicted label
        """
        feature_val_input = input_torch[self.feature_num]
        if(self.is_leaf()):
            return self.dominant_class
        else:
            if(feature_val_input < self.threshold_value):
                return self.node_left.evaluate_node(input_torch)
            else:
                return self.node_right.evaluate_node(input_torch)
        

class CART:
    def __init__(self, dataset_torch, max_CART_depth, min_observations = 2, use_gini=True):
        """
        CART has only one root node
        """
        #min observations per node
        self.min_observations = min_observations
        self.root = Node_CART(num_classes = 4, ref_CART = self, current_depth = 0, use_gini=use_gini)
        self.max_CART_depth = max_CART_depth
        self.list_selected_features = []
        
    def get_root(self):
        """
        Gets tree root
        """
        return self.root
    
    def get_min_observations(self):
        """
        return min observations per node
        """
        return self.min_observations
    
    def get_max_depth(self):
        """
        Gets the selected max depth of the tree
        """
        return self.max_CART_depth
    
    def build_CART(self, data_torch):
        """
        Build CART from root
        """
        self.list_selected_features = self.root.create_with_children(data_torch, current_depth = 0)
    
    def to_xml(self, xml_file_name):
        """
        write Xml file with tree content
        """
        str_nodes = self.root.to_xml()
        file = open(xml_file_name,"w+") 
        file.write(str_nodes)
        file.close()
        return str_nodes
    
    
    def evaluate_input(self, input_torch):
        """
        Evaluate a specific input in the tree and get the predicted class
        """
        return self.root.evaluate_node(input_torch)
        
    
def train_CART(dataset_torch, name_xml = "", max_CART_depth = 3, min_obs_per_leaf = 2, use_gini = True): 
    """
    Train CART model
    """
    tree = CART(dataset_torch = dataset_torch, max_CART_depth = max_CART_depth, min_observations =  min_obs_per_leaf, use_gini = use_gini)
    tree.build_CART(dataset_torch)
    if(not name_xml == ""):
        tree.to_xml(name_xml)
    return tree

def test_CART(tree, testset_torch):
    """
    Test a previously built CART
    """
    n = testset_torch.shape[0]
    c = 0
    for value in testset_torch:
        result = tree.evaluate_input(value)
        if result == value[-1]:
            c += 1
    return c/n


# Titanic Example
#data_test = torch.tensor([[3, 22, 7.2, 0], [1, 38, 71.3, 0], [3, 26, 7.9, 1],[1, 35, 53.1, 0]])        
#testset = torch.tensor([[3, 21, 7.4, 0],[1, 40, 70.4, 0], [3, 27, 9, 1]]) 
#tree = train_CART(data_test, name_xml = "CART_example.xml", use_gini = False)
#acc = test_CART(tree, data_test)

# Wifi Example
tree_gini = train_CART(dataset_torch[:4], name_xml = "CART_example.xml", use_gini = True)
tree_entropy = train_CART(dataset_torch, name_xml = "CART_example.xml", use_gini = False)
acc = test_CART(tree_gini, dataset_torch)

print("Accuracy:", acc)
        

    
        

data_torch tensor([[-64., -56., -61., -66., -71., -82., -81.,   1.],
        [-68., -57., -61., -65., -71., -85., -85.,   1.],
        [-63., -60., -60., -67., -76., -85., -84.,   1.],
        [-61., -60., -68., -62., -77., -90., -80.,   1.]], dtype=torch.float64)
------------- Feature id: 0 -------------
values_sorted tensor([-68., -64., -63., -61.], dtype=torch.float64)
------------- Feature id: 0, Value: -64.0 -------------
Data < -64.0: tensor([[-68., -57., -61., -65., -71., -85., -85.,   1.]], dtype=torch.float64)
Data > -64.0: tensor([[-64., -56., -61., -66., -71., -82., -81.,   1.],
        [-63., -60., -60., -67., -76., -85., -84.,   1.],
        [-61., -60., -68., -62., -77., -90., -80.,   1.]], dtype=torch.float64)
gini: -1.9073486328125e-06
gini: -1.9073486328125e-06
left_entropy:  -1.9073486328125e-06
right_entropy:  -1.9073486328125e-06
Ponderate:  -1.9073486328125e-06
------------- Feature id: 0, Value: -63.0 -------------
Data < -63.0: tensor([[-64., -56., -61., -66., -7

left_entropy:  0.7817676067352295
right_entropy:  1.9959123134613037
Ponderate:  1.9279202098846435
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 -------------
Continue value: -65.0
------------- Feature id: 0, Value: -65.0 

------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue value: -63.0
------------- Feature id: 0, Value: -63.0 -------------
Continue

Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 -------------
Continue value: -59.0
------------- Feature id: 0, Value: -59.0 

Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 -------------
Continue value: -51.0
------------- Feature id: 0, Value: -51.0 

...

Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 -------------
Continue value: -66.0
------------- Feature id: 4, Value: -66.0 

Data < -87.0: tensor([[-61., -60., -68., -62., -77., -90., -80.,   1.],
        [-64., -55., -63., -66., -76., -88., -83.,   1.],
        [-61., -59., -65., -63., -74., -89., -87.,   1.],
        [-66., -59., -64., -68., -68., -97., -83.,   1.],
        [-67., -57., -64., -71., -75., -89., -87.,   1.],
        [-70., -62., -68., -65., -81., -89., -83.,   1.],
        [-67., -59., -62., -66., -80., -96., -82.,   1.],
        [-66., -59., -65., -68., -75., -88., -84.,   1.],
        [-67., -59., -62., -65., -71., -91., -84.,   1.],
        [-66., -62., -64., -68., -73., -89., -83.,   1.],
        [-68., -58., -65., -67., -83., -89., -86.,   1.],
        [-65., -58., -64., -69., -81., -88., -90.,   1.],
        [-65., -56., -63., -71., -77., -89., -85.,   1.],
        [-64., -59., -65., -70., -84., -90., -89.,   1.],
        [-64., -56., -64., -70., -80., -91., -84.,   1.],
        [-68., -57., -64., -68., -77., -88., -85.,   1.],
        [-67., -56., -65., -68., -82., -96., -89.,   1.],


Data < -76.0: tensor([[-64., -56., -61.,  ..., -82., -81.,   1.],
        [-68., -57., -61.,  ..., -85., -85.,   1.],
        [-63., -60., -60.,  ..., -85., -84.,   1.],
        ...,
        [-61., -55., -55.,  ..., -83., -92.,   4.],
        [-56., -55., -50.,  ..., -84., -86.,   4.],
        [-58., -56., -46.,  ..., -84., -87.,   4.]], dtype=torch.float64)
Data > -76.0: tensor([[-60., -55., -58., -57., -75., -74., -82.,   1.],
        [-61., -56., -57., -56., -75., -74., -81.,   1.],
        [-57., -53., -56., -58., -68., -75., -80.,   1.],
        [-58., -54., -52., -61., -74., -75., -82.,   1.],
        [-59., -51., -58., -57., -64., -76., -85.,   1.],
        [-60., -53., -59., -64., -65., -76., -81.,   1.],
        [-62., -55., -59., -63., -72., -76., -87.,   1.],
        [-59., -52., -61., -61., -76., -75., -78.,   1.],
        [-59., -56., -62., -59., -67., -75., -78.,   1.],
        [-60., -57., -58., -59., -70., -76., -80.,   1.],
        [-61., -53., -52., -60., -72., -75., 

Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 -------------
Continue value: -84.0
------------- Feature id: 6, Value: -84.0 

Accuracy: 0.25
